In [249]:
import warnings
import os
import numpy as np
import pandas as pd

warnings.filterwarnings('ignore')

# Set seed
np.random.seed(42)

# Set working directory
os.chdir(r"..") # should be the git repo root directory
print("Current working directory: " + os.getcwd())
repo_name = 'net-load-forecasting'
assert os.getcwd()[-len(repo_name):] == "net-load-forecasting", "Working directory is not the git repo root directory"



from bin.bess import *

Current working directory: /Users/nikolaushouben/Desktop/net-load-forecasting


# BESS in each household

This section generates the modified netload profile for each household (and aggregated) based on a local, rule-based control of a BESS in each household. 

The control strategy is based on the following rules, and is sometimes referred to 'surplus charging' in the literature (see e.g. [1]):

- Satisfy the load of the household with the PV generation first
- Charge the battery with the surplus PV generation
- Discharge the battery to satisfy the load of the household when the PV generation is not enough
- Import from the grid to satisfy the load of the household when the battery is empty and the PV generation is not enough



[1] Houben, N., Cosic, A., Stadler, M., Mansoor, M., Zellinger, M., Auer, H., ... & Haas, R. (2023). Optimal dispatch of a multi-energy system microgrid under uncertainty: A renewable energy community in Austria. Applied Energy, 337, 120913.



In [255]:
for timestep in ["1min","15min"]:
    df_loads = pd.read_hdf("data/clean_data/data_net_load_forecasting.h5", key=f"{timestep}/loads") / 1000
    df_pvs = pd.read_hdf("data/clean_data/data_net_load_forecasting.h5", key=f"{timestep}/pvs") / 1000
    df_netload_wo_bess = pd.read_hdf("data/clean_data/data_net_load_forecasting.h5", key=f"{timestep}/netload") / 1000
    df_prices = pd.read_hdf("data/clean_data/data_net_load_forecasting.h5", key="imbalance_price")

    rbc = RuleBasedController(df_loads, df_pvs, 5, 1) # assumption for now: 5kWh capacity bess, with c-rate of 1
    results_array = rbc.run()
    df_results = pd.DataFrame(results_array[:,0,:], columns=["nl[kW]", "bess_p[kW]", "bess_en[kWh]", "load[kW]", "pv[kW]"])

    df_netload_with_bess = pd.DataFrame(results_array[:,:,0], columns = [f"nl_{i}" for i in range(results_array.shape[1])], index = df_netload_wo_bess.index).sum(axis = 1).to_frame(name = "netload_with_bess")
    with pd.HDFStore("/Users/nikolaushouben/Desktop/net-load-forecasting/data/clean_data/data_net_load_forecasting.h5", mode = "a") as store:
        store.put(f"{timestep}/netload_with_bess", df_netload_with_bess, format = "table")

    if timestep == "15min":
        fig = px.line(pd.concat([df_netload_wo_bess, df_netload_with_bess], axis = 1))
        fig.show()


Initialized batteries with capacities: [5 5 5 5 5 5 5 5 5 5 5 5 5 5 5 5 5 5 5 5], max power: [5 5 5 5 5 5 5 5 5 5 5 5 5 5 5 5 5 5 5 5], energies: [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
Initialized batteries with capacities: [5 5 5 5 5 5 5 5 5 5 5 5 5 5 5 5 5 5 5 5], max power: [5 5 5 5 5 5 5 5 5 5 5 5 5 5 5 5 5 5 5 5], energies: [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
